### Загрузка архивов с boto3

In [2]:
import os
import boto3

# Получение значений из переменных окружения
aws_key_id = os.getenv('AWS_ACCESS_KEY_ID')
aws_secret_key = os.getenv('AWS_SECRET_ACCESS_KEY')

s3 = boto3.client('s3',
                  endpoint_url="https://storage.yandexcloud.net",
                  aws_access_key_id=aws_key_id,
                  aws_secret_access_key=aws_secret_key)

# Пример использования
bucket_name = 'afana-propdoc-production'
s3_file_key = 'processed_archived_documents/SP-51.13330.2011.pdf.zip'  
local_file_name = 'SP-51.13330.2011.pdf.zip '


# Скачиваем файл
s3.download_file(bucket_name, s3_file_key, local_file_name)

### Тестирование различных вариантов обработки MD

In [ ]:
import os
import re
from langchain.prompts import MarkdownRenderer

# Функция для разбиения Markdown текста по заголовкам и извлечения их
def extract_headers(md_text):
    headers = []
    for line in md_text.splitlines():
        if line.startswith("#"):  # Заголовки в Markdown начинаются с #
            headers.append(line.strip())
    return headers

# Функция для чтения и объединения всех файлов из папки md_from_pdf
def combine_md_files(md_folder_path):
    combined_md = ""
    page_map = {}
    
    for filename in sorted(os.listdir(md_folder_path)):  # Сортируем файлы по страницам
        if filename.endswith('.md'):
            page_num = re.search(r'page_(\d+)', filename).group(1)  # Извлекаем номер страницы
            with open(os.path.join(md_folder_path, filename), 'r', encoding='utf-8') as file:
                text = file.read()
                combined_md += f"\n\n## Page {page_num}\n\n" + text  # Добавляем текст с номером страницы
                page_map[page_num] = text  # Запоминаем текст для каждой страницы
    return combined_md, page_map

# Функция для обработки текста с использованием LangChain
def process_with_langchain(combined_md):
    renderer = MarkdownRenderer()
    structured_data = renderer.render(combined_md)  # Преобразуем Markdown в структурированные данные
    return structured_data

# Основная функция
def create_database(md_folder):
    combined_md, page_map = combine_md_files(md_folder)  # Сначала объединяем все Markdown-файлы
    
    # Далее обрабатываем полученный Markdown через LangChain для извлечения структур
    structured_data = process_with_langchain(combined_md)
    
    database = []
    
    for page_num, text in page_map.items():
        headers = extract_headers(text)  # Функция для извлечения заголовков
        page_data = {
            "page": int(page_num),
            "text": text,
            "metadata": {
                "headers": headers
            }
        }
        database.append(page_data)
    
    return database

# Пример использования
md_folder = '../RAG/SP-60.13330.2020.pdf/md_from_pdf'

database = create_database(md_folder)

# Пример вывода результата
for page in database:
    print(f"Страница {page['page']}:")
    print(f"Заголовки: {page['metadata']['headers']}")
    print("-" * 50)


In [9]:
from langchain_community.document_loaders import UnstructuredMarkdownLoader

markdown_path = "../RAG/Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf/md_from_pdf/page_1.md"
loader = UnstructuredMarkdownLoader(markdown_path)

data = loader.load()
print(data[0].page_content)

In [ ]:
import markdown
from langchain.document_loaders import UnstructuredHTMLLoader

# Функция для конвертации Markdown в HTML
def markdown_to_html(md_text):
    return markdown.markdown(md_text)

# Пример markdown текста
md_text = """
# ПРАВИТЕЛЬСТВО РОССИЙСКОЙ ФЕДЕРАЦИИ

# ПОСТАНОВЛЕНИЕ

# от 16 сентября 2020 г. М 1479

# ОБ УТВЕРЖДЕНИИ ПРАВИЛ
ПРОТИВОПОЖАРНОГО РЕЖИМА В РОССИЙСКОЙ
ФЕДЕРАЦИИ

(в ред. Постановлений Правительства РФ от 31.12.2020 М 2463, от 21.05.2021 М 766, от

 

24.10.2022 М 1885, от 30.03.2023 М 510)

В соответствии со статьей 16 Федерального закона "О пожарной безопасности"
Правительство Российской Федерации постановляет:

1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.

2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря
2026 г. включительно.

В соответствии со статьей 16 Федерального закона "О пожарной безопасности"
Правительство Российской Федерации постановляет:

1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.

2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря
2026 г. включительно.

Председатель Правительства

Россиискои Федерации

М. МИШУСТИН

УТВЕРЖДЕНЫ

постановлением Правительства

Российской Федерации

от 16 сентября 2020 г. М 1479

# ПРАВИЛА ПРОТИВОПОЖАРНОГО РЕЖИМА В

РОССИЙСКОЙ ФЕДЕРАЦИИ

(в ред. Постановлений Правительства РФ от 31.12.2020 М 2463, от 21.05.2021 М 766, от

 

24.10.2022 М 1885, от 30.03.2023 М 510)


"""

# Конвертируем markdown в HTML
html_content = markdown_to_html(md_text)

# Сохраняем HTML во временный файл (или можно передать напрямую)
with open("temp.html", "w", encoding="utf-8") as f:
    f.write(html_content)

# Загружаем HTML в LangChain для обработки
loader = UnstructuredHTMLLoader("temp.html")
documents = loader.load()

# Выводим результат
for doc in documents:
    print(doc.page_content)
html_content

In [12]:
import markdown
from bs4 import BeautifulSoup
from langchain.text_splitter import HTMLHeaderTextSplitter, RecursiveCharacterTextSplitter

# Пример markdown текста
md_text = """
# ПРАВИТЕЛЬСТВО РОССИЙСКОЙ ФЕДЕРАЦИИ

# ПОСТАНОВЛЕНИЕ

# от 16 сентября 2020 г. М 1479

# ОБ УТВЕРЖДЕНИИ ПРАВИЛ
ПРОТИВОПОЖАРНОГО РЕЖИМА В РОССИЙСКОЙ
ФЕДЕРАЦИИ

(в ред. Постановлений Правительства РФ от 31.12.2020 М 2463, от 21.05.2021 М 766, от

 

24.10.2022 М 1885, от 30.03.2023 М 510)

В соответствии со статьей 16 Федерального закона "О пожарной безопасности"
Правительство Российской Федерации постановляет:

1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.

2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря
2026 г. включительно.

В соответствии со статьей 16 Федерального закона "О пожарной безопасности"
Правительство Российской Федерации постановляет:

1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.

2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря
2026 г. включительно.

Председатель Правительства

Россиискои Федерации

М. МИШУСТИН

УТВЕРЖДЕНЫ

постановлением Правительства

Российской Федерации

от 16 сентября 2020 г. М 1479

# ПРАВИЛА ПРОТИВОПОЖАРНОГО РЕЖИМА В

РОССИЙСКОЙ ФЕДЕРАЦИИ

(в ред. Постановлений Правительства РФ от 31.12.2020 М 2463, от 21.05.2021 М 766, от

 

24.10.2022 М 1885, от 30.03.2023 М 510)


"""

# 1. Конвертируем Markdown в HTML
html_content = markdown.markdown(md_text, extensions=['extra'])

# 2. Парсим HTML и подготавливаем документ для разделения
soup = BeautifulSoup(html_content, "html.parser")
html_cleaned = str(soup)

# 3. Указываем заголовки для разбиения (h1, h2, h3)
headers_to_split_on = [
    ("h1", "Header 1"),
    ("h2", "Header 2"),
    ("h3", "Header 3"),
    ("h4", "Header 4")
]

# 4. Используем HTMLHeaderTextSplitter для разбиения по заголовкам
html_splitter = HTMLHeaderTextSplitter(headers_to_split_on=headers_to_split_on)

# split_text разделяет текст по указанным заголовкам
html_header_splits = html_splitter.split_text(html_cleaned)

# 5. Настраиваем RecursiveCharacterTextSplitter для более мелкого разделения по размеру блоков
chunk_size = 1800
chunk_overlap = 200
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=chunk_size, chunk_overlap=chunk_overlap
)

# 6. Применяем RecursiveCharacterTextSplitter для деления на части
splits = text_splitter.split_documents(html_header_splits)

In [ ]:
splits

### Создание единой системы с метаданными

In [8]:
import os
from langchain_community.document_loaders import UnstructuredMarkdownLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

# Папка, где хранятся документы
base_folder = '../RAG'

# Список документов
arr = [
    'Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf',
    'SP 50.13330.2012.pdf',
    'SP-60.13330.2020.pdf'
]

# Функция для обработки Markdown файлов в папках
def process_markdown_files():
    for doc_name in arr:
        # Определяем путь к папке с документами
        doc_folder = os.path.join(base_folder, doc_name.replace(".pdf", ""), "md_from_pdf")
        
        if os.path.exists(doc_folder):
            for md_file in os.listdir(doc_folder):
                if md_file.endswith('.md'):
                    md_file_path = os.path.join(doc_folder, md_file)
                    
                    # Загружаем файл с помощью LangChain
                    with open(md_file_path, 'r', encoding='utf-8') as f:
                        md_content = f.read()
                    
                    # Используем LangChain для обработки текста
                    loader = UnstructuredMarkdownLoader(md_file_path)
                    documents = loader.load()
                    
                    # Разделяем документ на страницы
                    text_splitter = RecursiveCharacterTextSplitter(chunk_size=2000)
                    pages = text_splitter.split_documents(documents)
                    
                    # Добавляем метаданные
                    for i, page in enumerate(pages):
                        page.metadata = {
                            "filename": md_file,
                            "page_number": i + 1,
                            "source": doc_name
                        }
                

a = process_markdown_files()

### Хороший вариант 

In [ ]:
import os
from langchain.docstore.document import Document
import re
from typing import List

def extract_metadata_from_markdown(markdown_text: str) -> List[str]:
    """
    Извлекает заголовки из Markdown текста и убирает символы #.
    """
    return [re.sub(r'^#+\s*', '', header) for header in re.findall(r'(^#+ .*)', markdown_text, re.MULTILINE)]

def process_markdown_with_metadata(file_content: str, file_name: str, folder_path: str) -> Document:
    """
    Создаёт объект Document с метаданными для Markdown файла.
    """
    metadata = {
        "pdf_file": folder_path.split(os.sep)[-2],
        "pages": int(file_name.split('_')[1].replace('.md', '')),
        "headers": extract_metadata_from_markdown(file_content),
        "source": file_name
    }
    return Document(page_content=file_content, metadata=metadata)

def get_documents_from_folder(folder_path: str) -> List[Document]:
    """
    Создаёт список объектов Document для всех Markdown файлов в указанной папке.
    """
    documents = []
    filenames = [f for f in os.listdir(folder_path) if f.endswith(".md")]
    filenames.sort(key=lambda f: int(f.split('_')[1].replace('.md', '')))
    
    for filename in filenames:
        with open(os.path.join(folder_path, filename), 'r', encoding='utf-8') as f:
            file_content = f.read()
        documents.append(process_markdown_with_metadata(file_content, filename, folder_path))
    
    return documents

# Список документов
arr = [
    'Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf',
    'SP 50.13330.2012.pdf',
    'SP-60.13330.2020.pdf'
]

base_dir = '../RAG/'
all_documents = []

# Перебираем каждый документ в списке
for document_name in arr:
    folder_path = os.path.join(base_dir, document_name, 'md_from_pdf')
    if os.path.exists(folder_path):
        all_documents.extend(get_documents_from_folder(folder_path))

# all_documents содержит все файлы
all_documents

In [12]:
import os
from langchain.docstore.document import Document
import re

def extract_metadata_from_markdown(markdown_text):
    """
    Извлекает заголовки из Markdown и убирает символы #.
    """
    return [re.sub(r'^#+\s*', '', header) for header in re.findall(r'(^#+ .*)', markdown_text, re.MULTILINE)]

def get_unstructured_data_paths(page_folder):
    """
    Собирает пути к изображениям, таблицам и формулам для указанной страницы из папки unstructured_data.
    """
    path_png = os.path.join(page_folder.split(os.sep)[-5], page_folder.split(os.sep)[-2], page_folder.split(os.sep)[-1])
    add_metadata = {
        'Picture': [],
        'Table': [],
        'Formula': []
    }
    for data_type in add_metadata.keys():
        data_folder = os.path.join(page_folder, data_type)
        if os.path.exists(data_folder):
            for filename in os.listdir(data_folder):
                if filename.endswith(".png"):
                    add_metadata[data_type].append(os.path.join(path_png, data_type, filename))
    return add_metadata

def process_markdown_with_metadata(file_content, file_name, folder_path):
    """
    Создаёт объект Document с метаданными для Markdown файла, включая пути к изображениям, таблицам и формулам.
    """
    page_number = int(file_name.split('_')[1].replace('.md', ''))
    page_folder = os.path.join(folder_path, '..', 'unstructured_data', f'page_{page_number}')
    
    metadata = {
        "pdf_file": folder_path.split(os.sep)[-2],
        "pages": page_number,
        "headers": extract_metadata_from_markdown(file_content),
        "source_md": file_name
    }
    
    metadata.update(get_unstructured_data_paths(page_folder))
    
    return Document(page_content=file_content, metadata=metadata)

def get_documents_from_folder(folder_path):
    """
    Собирает список документов для всех Markdown файлов в указанной папке.
    """
    documents = []
    filenames = [f for f in os.listdir(folder_path) if f.endswith(".md")]
    filenames.sort(key=lambda f: int(f.split('_')[1].replace('.md', '')))
    
    for filename in filenames:
        with open(os.path.join(folder_path, filename), 'r', encoding='utf-8') as f:
            file_content = f.read()
        documents.append(process_markdown_with_metadata(file_content, filename, folder_path))

    return documents

# Список документов
# folders = [
#     'Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf',
#     'SP 50.13330.2012.pdf',
#     'SP-60.13330.2020.pdf'
# ]

# folders = [
#     'SP-60.13330.2020.pdf'
# ]

def get_all_folders(directory):
    all_entries = os.listdir(directory)
    folders = [entry for entry in all_entries if os.path.isdir(os.path.join(directory, entry))]
    return folders

folders = get_all_folders('../RAG/processed_docs')


base_dir = '../Downloads/RAG/processed_docs'
all_documents = []

# Перебираем каждый документ, собираем Markdown и добавляем метаданные
for document_name in folders:
    folder_path = os.path.join(base_dir, document_name, 'md_from_pdf')
    if os.path.exists(folder_path):
        all_documents.extend(get_documents_from_folder(folder_path))

# Все документы с метаданными готовы
all_documents

[Document(page_content='# ПРАВИТЕЛЬСТВО РОССИЙСКОЙ ФЕДЕРАЦИИ\n\nПОСТАНОВЛЕНИЕ\nот 16 февраля 2008 г. М 87\n\n## О СОСТАВЕ РАЗДЕЛОВ ПРОЕКТНОЙ ДОКУМЕНТАЦИИ\nИ ТРЕБОВАНИЯХ К ИХ СОДЕРЖАНИЮ\n\nСписок изменяющих документов\n(в ред. Постановлений Правительства РФ от 18.05.2009 М 427,\nот 21.12.2009 М 1044, от 13.04.2010 М 2395, от 07.12.2010 М 1006,\nот 15.02.2011 М 73, от 25.06.2012 М 628, от 02.08.2012 М 788,\nот 22.04.2013 М 360, от 30.04.2013 М 382, от 08.08.2013 М 679,\nот 26.03.2014 М 230, от 10.12.2014 М 1346, от 28.07.2015 М 767,\nот 27.10.2015 М 1147, от 23.01.2016 М 29, от 12.11.2016 М 1159,\nот 28.01.2017 М 95, от 28.04.2017 М 506, от 12.05.2017 М 563,\nот 07.07.2017 М 806, от 08.09.2017 М 1081, от 13.12.2017 М 1541,\nот 15.03.2018 М 257, от 21.04.2018 М 479, от 17.09.2018 М 1096,\nот 06.07.2019 М 864, от 28.04.2020 М 598, от 01.10.2020 М 1590,\nот 21.12.2020 М 2184, от 09.04.2021 М 567, от 15.07.2021 М 1197,\nот 01.12.2021 М 2161, от 20.04.2022 М 711, от 27.05.2022 М 963)\n\nВ соо

In [14]:
len(all_documents)

417

In [15]:
import os
from langchain.docstore.document import Document
import re

def extract_metadata_from_markdown(markdown_text):
    """
    Извлекает заголовки из Markdown и убирает символы #.
    """
    return [re.sub(r'^#+\s*', '', header) for header in re.findall(r'(^#+ .*)', markdown_text, re.MULTILINE)]

def get_unstructured_data_paths(page_folder):
    """
    Собирает пути к изображениям, таблицам и формулам для указанной страницы из папки unstructured_data.
    """
    path_png = os.path.join(page_folder.split(os.sep)[-5], page_folder.split(os.sep)[-2], page_folder.split(os.sep)[-1])
    add_metadata = {
        'Picture': [],
        'Table': [],
        'Formula': []
    }
    for data_type in add_metadata.keys():
        data_folder = os.path.join(page_folder, data_type)
        if os.path.exists(data_folder):
            for filename in os.listdir(data_folder):
                if filename.endswith(".png"):
                    add_metadata[data_type].append(os.path.join(path_png, data_type, filename))
    return add_metadata

def process_markdown_with_metadata(file_content, file_name, folder_path, previous_content=None, overlap_size=100):
    """
    Создаёт объект Document с метаданными для Markdown файла, включая пути к изображениям, таблицам и формулам.
    Добавляет пересечение текста с предыдущей страницей.
    """
    page_number = int(file_name.split('_')[1].replace('.md', ''))
    page_folder = os.path.join(folder_path, '..', 'unstructured_data', f'page_{page_number}')
    
    # Добавляем overlap с предыдущей страницей, если она есть
    if previous_content:
        file_content = previous_content[-overlap_size:] + "\n" + file_content
    
    metadata = {
        "pdf_file": folder_path.split(os.sep)[-2],
        "pages": page_number,
        "headers": extract_metadata_from_markdown(file_content),
        "source_md": file_name
    }
    
    metadata.update(get_unstructured_data_paths(page_folder))
    
    return Document(page_content=file_content, metadata=metadata)

def get_documents_from_folder(folder_path, overlap_size=100):
    """
    Собирает список документов для всех Markdown файлов в указанной папке с пересечением (overlap) между страницами.
    """
    documents = []
    filenames = [f for f in os.listdir(folder_path) if f.endswith(".md")]
    filenames.sort(key=lambda f: int(f.split('_')[1].replace('.md', '')))
    
    previous_content = None  # Храним текст предыдущей страницы
    
    for filename in filenames:
        with open(os.path.join(folder_path, filename), 'r', encoding='utf-8') as f:
            file_content = f.read()
        
        doc = process_markdown_with_metadata(file_content, filename, folder_path, previous_content, overlap_size)
        documents.append(doc)
        
        # Обновляем предыдущий контент для следующей страницы
        previous_content = file_content

    return documents

# Список документов
arr = [
    'Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf',
    'SP 50.13330.2012.pdf',
    'SP-60.13330.2020.pdf'
]

base_dir = '../RAG/'
all_documents = []

# Перебираем каждый документ, собираем Markdown и добавляем метаданные
for document_name in arr:
    folder_path = os.path.join(base_dir, document_name, 'md_from_pdf')
    if os.path.exists(folder_path):
        all_documents.extend(get_documents_from_folder(folder_path, overlap_size=100))

# Все документы с метаданными и пересечением между страницами готовы
all_documents


[Document(page_content='# ПРАВИТЕЛЬСТВО РОССИЙСКОЙ ФЕДЕРАЦИИ\n\n# ПОСТАНОВЛЕНИЕ\n\n# от 16 сентября 2020 г. М 1479\n\n# ОБ УТВЕРЖДЕНИИ ПРАВИЛ\nПРОТИВОПОЖАРНОГО РЕЖИМА В РОССИЙСКОЙ\nФЕДЕРАЦИИ\n\n(в ред. Постановлений Правительства РФ от 31.12.2020 М 2463, от 21.05.2021 М 766, от\n\n \n\n24.10.2022 М 1885, от 30.03.2023 М 510)\n\nВ соответствии со статьей 16 Федерального закона "О пожарной безопасности"\nПравительство Российской Федерации постановляет:\n\n1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.\n\n2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря\n2026 г. включительно.\n\nВ соответствии со статьей 16 Федерального закона "О пожарной безопасности"\nПравительство Российской Федерации постановляет:\n\n1. Утвердить прилагаемые Правила противопожарного режима в Российской Федерации.\n\n2. Настоящее постановление вступает в силу с 1 января 2021 г. и действует до 31 декабря\n2026 г. включительно.\n\nПредседатель Прави

In [16]:
len(all_documents)

329

### Векторизация 

In [ ]:
from sentence_transformers import SentenceTransformer

# Загружаем модель
embedding_model = SentenceTransformer('all-mpnet-base-v2')

# Векторизируем тексты
texts = all_documents[:10]
embeddings = embedding_model.encode([texts])

In [5]:
# OpenAI proxy
import os
from langchain_openai import OpenAIEmbeddings
from langchain_openai import ChatOpenAI

# Получение переменных окружения
api_key = os.getenv("OPENAI_API_KEY")
base_url = os.getenv("OPENAI_BASE_URL")

# Установка переменных окружения
os.environ["OPENAI_API_KEY"] = api_key
os.environ["OPENAI_BASE_URL"] = base_url

# OpenAI 
llm = ChatOpenAI(model_name="gpt-3.5-turbo-0125")
embedding_model = OpenAIEmbeddings()

In [ ]:
import os
from langchain.vectorstores import Qdrant
from qdrant_client import QdrantClient

# Получение переменных окружения
url = os.getenv("QDRANT_URL")
api_key = os.getenv("QDRANT_API_KEY")
collection_name = "SP-60.13330.2020"

# Подключение к Qdrant
qdrant_client = QdrantClient(url=url, api_key=api_key)

# Используем OllamaEmbeddings для векторизации
# from langchain_community.embeddings import OllamaEmbeddings
# embedding_model = OllamaEmbeddings(model="llama3.1")

# Создание базы данных в Qdrant и загрузка данных
vector_store = Qdrant.from_documents(
    all_documents[:10],
    embedding_model,
    url=url,
    api_key=api_key,
    collection_name=collection_name
)
print("Документы успешно добавлены в Qdrant.")

### Подключение к Qdrant и поиск 

In [44]:
import os
from langchain.vectorstores import Qdrant
from qdrant_client import QdrantClient

# Получение переменных окружения
url = os.getenv("QDRANT_URL")
api_key = os.getenv("QDRANT_API_KEY")
collection_name = "new_docs"

# Создаем клиент для подключения к Qdrant
qdrant_client = QdrantClient(url=url, api_key=api_key)

# Создаем объект OllamaEmbeddings
embedding_model = OllamaEmbeddings(model="llama3.1")

# Создаем объект Qdrant для взаимодействия с коллекцией
vector_store = Qdrant(
    client=qdrant_client,
    collection_name=collection_name,
    embeddings=embedding_model  # Передаем объект embeddings
)

In [46]:
query = "Что включает в себя ОСТ 10616-2015?"
# Векторизуем запрос
query_vector = embedding_model.embed_query(query)
found_docs = vector_store.similarity_search(query_vector)

In [1]:
# OpenAI proxy
import os
from langchain_openai import OpenAIEmbeddings
from langchain_openai import ChatOpenAI

# Получение переменных окружения
api_key = os.getenv("OPENAI_API_KEY")
base_url = os.getenv("OPENAI_BASE_URL")

# Установка переменных окружения
os.environ["OPENAI_API_KEY"] = api_key
os.environ["OPENAI_BASE_URL"] = base_url

# OpenAI 
llm = ChatOpenAI(model_name="gpt-3.5-turbo-0125")
embedding_model = OpenAIEmbeddings()

In [ ]:
from qdrant_client import QdrantClient
from fastembed import FastEmbed

# Инициализация клиента Qdrant
qdrant_client = QdrantClient(url="http://localhost:6333")

# Инициализация FastEmbed
embedder = FastEmbed(model="multi-modal")

# Векторизация текстов и изображений
text_embedding = embedder.embed_text("привет")
image_embedding = embedder.embed_image("../RAG/Postanovlenie_Pravitelstva_RF_ot_16_09_2020_N_1479_Ob_utverzhdenii.pdf/unstructured_data/page_90/Table/image_1.png")

# Загрузка в Qdrant
qdrant_client.upload_collection(
    collection_name="multimodal_search",
    vectors=[text_embedding, image_embedding],
    payloads=[{"type": "text"}, {"type": "image"}],
    batch_size=64
)


In [48]:
found_docs = vector_store.similarity_search_with_score(query_vector)